In [10]:
from telethon import TelegramClient, events
from telethon.tl.functions.messages import GetDialogsRequest
from telethon.tl.types import InputPeerEmpty, Channel, User, Chat
import os
from dotenv import load_dotenv
import asyncio

load_dotenv()

# Telegram API 정보
api_id = os.getenv('TELEGRAM_API_ID')
api_hash = os.getenv('TELEGRAM_API_HASH')
phone = os.getenv('TELEGRAM_PHONE')

In [12]:
client = TelegramClient('telegram_session', api_id, api_hash)

await client.connect()

if not await client.is_user_authorized():
    await client.send_code_request(phone)
    print(f"{phone}으로 코드를 보냈습니다. 코드를 입력하세요:")
    code = input()
    await client.sign_in(phone, code)

Cannot get difference since the account is likely misusing the session: database is locked
Unhandled exception from keepalive_handle after cancelling <class '_asyncio.Task'> (<Task finished name='Task-245' coro=<UpdateMethods._keepalive_loop() done, defined at /Users/bongjoon/Desktop/project/ADA/sogood/.venv/lib/python3.13/site-packages/telethon/client/updates.py:481> exception=OperationalError('database is locked')>)
Traceback (most recent call last):
  File "/Users/bongjoon/Desktop/project/ADA/sogood/.venv/lib/python3.13/site-packages/telethon/helpers.py", line 176, in _cancel
    await task
  File "/Users/bongjoon/Desktop/project/ADA/sogood/.venv/lib/python3.13/site-packages/telethon/client/updates.py", line 517, in _keepalive_loop
    self._save_states_and_entities()
    ~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~^^
  File "/Users/bongjoon/Desktop/project/ADA/sogood/.venv/lib/python3.13/site-packages/telethon/client/telegrambaseclient.py", line 694, in _save_states_and_entities
    self.session

In [13]:
async def is_channel(chat):
    return isinstance(chat, Channel) and not chat.megagroup

import json
from pathlib import Path

current_dir = Path.cwd().parent
data_path = current_dir / "test" / "sectors.json"
async def categorize_message_by_sector(messages):
    with open(data_path, "r") as f:
        sectors = json.load(f)
    found_sectors = []
    for sector, keywords in sectors.items():
        for keyword in keywords:
            if keyword in messages:
                found_sectors.append(sector)
                break

    return list(set(found_sectors))

    

In [14]:
result = await client(GetDialogsRequest(
    offset_date=None,
    offset_id=0,
    offset_peer=InputPeerEmpty(),
    limit=200,
    hash=0
))

chats = result.chats
channels = []

for chat in chats:
    if await is_channel(chat):
        channels.append(chat)

print(f"단방향 채널 {len(channels)}개를 찾았습니다.")
print(channels)

단방향 채널 107개를 찾았습니다.
[<telethon.tl.types.Channel object at 0x1123cd450>, <telethon.tl.types.Channel object at 0x1123cd590>, <telethon.tl.types.Channel object at 0x1123cd6d0>, <telethon.tl.types.Channel object at 0x1123cd810>, <telethon.tl.types.Channel object at 0x1123cd950>, <telethon.tl.types.Channel object at 0x1123cda90>, <telethon.tl.types.Channel object at 0x1123cdbd0>, <telethon.tl.types.Channel object at 0x1123cdd10>, <telethon.tl.types.Channel object at 0x1123cde50>, <telethon.tl.types.Channel object at 0x1123cdf90>, <telethon.tl.types.Channel object at 0x1123ce0d0>, <telethon.tl.types.Channel object at 0x1123ce210>, <telethon.tl.types.Channel object at 0x1123ce350>, <telethon.tl.types.Channel object at 0x1123ce490>, <telethon.tl.types.Channel object at 0x1123ce710>, <telethon.tl.types.Channel object at 0x1123ce850>, <telethon.tl.types.Channel object at 0x1123ce990>, <telethon.tl.types.Channel object at 0x1123cead0>, <telethon.tl.types.Channel object at 0x1123cec10>, <telethon.

In [15]:
sector_data = {}
    
# 각 채널에서 메시지 가져오기
for channel in channels:
    try:
        messages = await client.get_messages(channel, limit=100)
        
        for msg in messages:
            if not msg.message:
                continue
            
            # 메시지 텍스트 기반으로 섹터 분류
            sectors = await categorize_message_by_sector(msg.message)
            
            if not sectors:  # 섹터가 없으면 다음 메시지로
                continue
            
            # 날짜 정보 (YYYY-MM-DD 형식)
            date_str = msg.date.strftime('%Y-%m-%d')
            
            # 각 섹터별로 메시지 저장
            for sector in sectors:
                if sector not in sector_data:
                    sector_data[sector] = {}
                
                if date_str not in sector_data[sector]:
                    sector_data[sector][date_str] = {}
                
                channel_title = channel.title
                if channel_title not in sector_data[sector][date_str]:
                    sector_data[sector][date_str][channel_title] = {
                        "posts": [],
                        "sentiment": {
                            "positive": 0,
                            "negative": 0,
                            "neutral": 0
                        }
                    }
                
                # 게시글 정보 저장
                post_info = {
                    "time": msg.date.strftime('%H:%M:%S'),
                    "content": msg.message,
                    "views": msg.views if hasattr(msg, 'views') else 0,
                    "replies": len(await client.get_messages(channel, reply_to=msg.id)) if msg.replies else 0
                }
                
                sector_data[sector][date_str][channel_title]["posts"].append(post_info)
        
        print(f"채널 '{channel.title}'에서 메시지를 가져왔습니다.")
        
    except Exception as e:
        print(f"채널 '{channel.title}' 처리 중 오류 발생: {e}")

# 각 섹터/날짜/채널에 대한 요약 정보 추가
for sector in sector_data:
    for date in sector_data[sector]:
        # 모든 채팅방 요약 정보 초기화
        all_channels_summary = {
            "total_posts": 0,
            "total_views": 0,
            "total_replies": 0,
            "channels_mentioned": 0
        }
        
        # 각 채널별 점수 계산
        for channel_title in sector_data[sector][date]:
            posts = sector_data[sector][date][channel_title]["posts"]
            total_views = sum(post["views"] for post in posts)
            total_replies = sum(post["replies"] for post in posts)
            
            # 언급도 및 점수 계산
            sector_data[sector][date][channel_title]["mentions"] = len(posts)
            sector_data[sector][date][channel_title]["score"] = len(posts) * 0.5 + total_views * 0.3 + total_replies * 0.2
            
            # 모든 채팅방 요약 정보 업데이트
            all_channels_summary["total_posts"] += len(posts)
            all_channels_summary["total_views"] += total_views
            all_channels_summary["total_replies"] += total_replies
            all_channels_summary["channels_mentioned"] += 1
        
        # 모든 채팅방 요약 추가
        sector_data[sector][date]["all_channels_summary"] = all_channels_summary

print(sector_data)

채널 '인포마켓 infomarket'에서 메시지를 가져왔습니다.
채널 '하나증권 리서치 중국/신흥국 전략 김경환'에서 메시지를 가져왔습니다.
채널 '훈쌤의 차트 공부방🥇'에서 메시지를 가져왔습니다.
채널 '중앙기획전략부'에서 메시지를 가져왔습니다.
채널 'TNBfolio'에서 메시지를 가져왔습니다.
채널 '기술적 분석으로 보는 주식시장'에서 메시지를 가져왔습니다.
채널 '블록미디어'에서 메시지를 가져왔습니다.
채널 'Hodolry의 텔레그램'에서 메시지를 가져왔습니다.
채널 '선진짱 주식공부방'에서 메시지를 가져왔습니다.
채널 '시장 이야기 by 제이슨'에서 메시지를 가져왔습니다.
채널 'Pluto Research'에서 메시지를 가져왔습니다.
채널 '코인유니브 지표＆차트시황 공유방'에서 메시지를 가져왔습니다.
채널 'PAUSE_CRYPTO_SIGNAL'에서 메시지를 가져왔습니다.
채널 '무팍’s Robo-gate. ver.2'에서 메시지를 가져왔습니다.
채널 '퀀텀 알고리즘'에서 메시지를 가져왔습니다.
채널 '습관이 부자를 만든다. 🧘'에서 메시지를 가져왔습니다.
채널 '에테르의 일본&미국 리서치'에서 메시지를 가져왔습니다.
채널 '재간둥이 송선생의 링크수집 창고'에서 메시지를 가져왔습니다.
채널 '그로쓰리서치(Growth Research) [독립리서치]'에서 메시지를 가져왔습니다.
채널 '탑클래스 투자'에서 메시지를 가져왔습니다.
채널 '참새선생의 주식공부방'에서 메시지를 가져왔습니다.
채널 '코백남 공지방'에서 메시지를 가져왔습니다.
채널 '화장품, 실리콘투, 뷰티'에서 메시지를 가져왔습니다.
채널 '기분좋은 마곤'에서 메시지를 가져왔습니다.
채널 'Brain and Body Research'에서 메시지를 가져왔습니다.
채널 '🔥PIVOT🔥 CEO의 말말말'에서 메시지를 가져왔습니다.
채널 '유진투자증권 코스닥벤처팀'에서 메시지를 가져왔습니다.
채널 'Airdrop Society'에서 메시지를 가져왔습니다.
채널 '투자자윤의 투자일지'에서 메시지를 가져왔습

In [16]:
with open('sector_analysis.json', 'w', encoding='utf-8') as f:
    json.dump(sector_data, f, ensure_ascii=False, indent=2)

print("분석 결과가 sector_analysis.json 파일로 저장되었습니다.")

print("\n각 섹터별 게시글 수:")
for sector in sector_data:
    total_posts = sum(
        data["all_channels_summary"]["total_posts"] 
        for date, data in sector_data[sector].items() 
        if "all_channels_summary" in data
    )
    print(f"{sector}: {total_posts}개 게시글")

분석 결과가 sector_analysis.json 파일로 저장되었습니다.

각 섹터별 게시글 수:
반도체: 432개 게시글
화장품: 244개 게시글
IT: 840개 게시글
자동차: 328개 게시글
은행: 312개 게시글
화학: 192개 게시글
이차전지: 145개 게시글
유통: 331개 게시글
전선: 256개 게시글
디스플레이: 70개 게시글
철강: 212개 게시글
건설: 225개 게시글
풍력: 244개 게시글
여행: 198개 게시글
수소: 35개 게시글
게임: 97개 게시글
원전: 249개 게시글
바이오: 379개 게시글
음식료: 115개 게시글
피부미용: 123개 게시글
방산: 196개 게시글
엔터: 179개 게시글
조선: 220개 게시글
보험: 70개 게시글
패션: 48개 게시글
임플란트: 23개 게시글


## 채팅 보는 불러오기

In [17]:
# chats = result.chats

# for i, chat in enumerate(chats):
#     try:
#         print(f"\n{i+1}. {chat.title}")
        
#         # 각 채팅방의 최근 메시지 가져오기
#         messages = await client.get_messages(chat, limit=2)
        
#         print(f"-- 최근 메시지 {len(messages)}개 --")
#         for msg in messages:
#             try:
#                 sender = await msg.get_sender()
                
#                 # 발신자 정보 처리
#                 if isinstance(sender, Channel):
#                     sender_name = sender.title
#                 elif isinstance(sender, User):
#                     sender_name = f"{sender.first_name} {sender.last_name if sender.last_name else ''}"
#                 else:
#                     sender_name = "알 수 없음"
                    
#                 content = msg.message if msg.message else "[미디어/특수 메시지]"
#                 print(f"[{msg.date}] {sender_name}: {content}")
#             except Exception as e:
#                 print(f"메시지 정보를 가져오는 중 오류 발생: {e}")
        
#     except Exception as e:
#         print(f"채팅방 정보를 가져오는 중 오류 발생: {e}")

In [18]:
# await client.disconnect()